In [1]:
import pandas as pd
import sqlite3


In [2]:
# 最大列数を None（制限なし）に
pd.set_option('display.max_columns', None)

# 最大行数も None に
pd.set_option('display.max_rows', None)


In [3]:
import os

# Notebook用にスクリプトの場所を手動で設定
BASE_DIR = r"C:\Users\image\Portfolio\Soccer analysis\soccer_pipeline\notebooks"

# プロジェクトのルート（soccer_pipeline）
ROOT_DIR = os.path.abspath(os.path.join(BASE_DIR, ".."))

#データベースのパス
DATABASE_PATH = os.path.join(ROOT_DIR,"db","matches.db")

# 過去シーズンデータファイルへのパス
SEASON_DATA_PATH = os.path.join(ROOT_DIR, "data", "premier_league.csv")

#このnotebookで作ったcsvを保存するパス
CSV_PATH = os.path.join(ROOT_DIR, "data", "processed_data.csv")


# データの読み込み

In [4]:

conn = sqlite3.connect(DATABASE_PATH)
c = conn.cursor()

# テーブル一覧
c.execute("SELECT name FROM sqlite_master WHERE type='table';")
print(c.fetchall())

# match_statisticsのカラム一覧
c.execute("PRAGMA table_info(match_statistics);")
print(c.fetchall())

conn.close()


[('matches',), ('match_statistics',), ('predictions',)]
[(0, 'fixture_id', 'INTEGER', 0, None, 1), (1, 'team_id', 'INTEGER', 0, None, 2), (2, 'team_name', 'TEXT', 0, None, 0), (3, 'shots', 'INTEGER', 0, None, 0), (4, 'shots_on_goal', 'INTEGER', 0, None, 0), (5, 'possession', 'REAL', 0, None, 0), (6, 'passes', 'INTEGER', 0, None, 0), (7, 'passes_accuracy', 'REAL', 0, None, 0), (8, 'fouls', 'INTEGER', 0, None, 0), (9, 'corners', 'INTEGER', 0, None, 0), (10, 'yellow_cards', 'INTEGER', 0, None, 0), (11, 'red_cards', 'INTEGER', 0, None, 0), (12, 'shots_off_goal', 'INTEGER', 0, None, 0)]


In [5]:


# DB接続
conn = sqlite3.connect(DATABASE_PATH)

# matches テーブルの全件確認
matches_df = pd.read_sql("SELECT * FROM matches", conn)
print(f"Total rows: {len(matches_df)}\n")

# match_statistics テーブルの全件確認
stats_df = pd.read_sql("SELECT * FROM match_statistics", conn)
print(f"Total rows: {len(stats_df)}\n")

conn.close()


Total rows: 1900

Total rows: 3300



In [6]:
matches_df.head()

fixture_id                       date  season  home_team       away_team  \
0      710556  2021-08-13T19:00:00+00:00    2021  Brentford         Arsenal   
1      710557  2021-08-14T14:00:00+00:00    2021    Burnley        Brighton   
2      710558  2021-08-14T14:00:00+00:00    2021    Chelsea  Crystal Palace   
3      710559  2021-08-14T14:00:00+00:00    2021    Everton     Southampton   
4      710560  2021-08-14T14:00:00+00:00    2021  Leicester          Wolves   

   home_score  away_score status  
0         2.0         0.0     FT  
1         1.0         2.0     FT  
2         3.0         0.0     FT  
3         3.0         1.0     FT  
4         1.0         0.0     FT

In [7]:
stats_df.head()

fixture_id  team_id          team_name  shots  shots_on_goal  possession  \
0      710556       55          Brentford    3.0              3        35.0   
1      710556       42            Arsenal    4.0              4        65.0   
2      710561       33  Manchester United    8.0              8        49.0   
3      710561       63              Leeds    3.0              3        51.0   
4      710565       38            Watford    7.0              7        38.0   

   passes  passes_accuracy  fouls  corners  yellow_cards  red_cards  \
0     309            201.0     12        2           NaN        NaN   
1     568            488.0      8        5           NaN        NaN   
2     422            334.0     11        5           1.0        NaN   
3     438            343.0      9        4           2.0        NaN   
4     317            234.0     18        2           3.0        NaN   

   shots_off_goal  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN

In [8]:
stats_df.isnull().sum()

fixture_id            0
team_id               0
team_name             0
shots              1020
shots_on_goal         0
possession            0
passes                0
passes_accuracy       0
fouls                 0
corners               0
yellow_cards        138
red_cards          2932
shots_off_goal     2280
dtype: int64

# match_dfとstats_dfを結合
#stats_dfはホームとアウェイの区別がないため、一度、teamカラムをすべてhome_teamにしたdfとすべてaway_teamにしたdfを作成し、  
それぞれのdfをhome_team、away_teamをkeyに結合することで、match_dfにhome_teamのstatsとaway_teamのstatsを結合する


In [9]:
#stats_dfはホームとアウェイの区別がないため、一度、teamカラムをすべてhome_teamにしたdfとすべてaway_teamにしたdfを作成し、それぞれのdfをhome_team、away_teamをkeyに結合することで、match_dfにhome_teamのstatsとaway_teamのstatsを結合する
# ホームチーム用統計
home_stats = stats_df.copy()
home_stats = home_stats.rename(columns={
    "team_name": "home_team_name",
    "shots": "home_shots",
    "shots_on_goal": "home_shots_on_goal",
    "possession": "home_possession",
    "passes": "home_passes",
    "passes_accuracy": "home_passes_accuracy",
    "fouls": "home_fouls",
    "corners": "home_corners",
    "yellow_cards": "home_yellow_cards",
    "red_cards": "home_red_cards"
})
home_stats = home_stats[["fixture_id", "home_team_name", "home_shots", "home_shots_on_goal",
                         "home_possession", "home_passes", "home_passes_accuracy",
                         "home_fouls", "home_corners", "home_yellow_cards", "home_red_cards"]]

In [10]:
home_stats.head()

fixture_id     home_team_name  home_shots  home_shots_on_goal  \
0      710556          Brentford         3.0                   3   
1      710556            Arsenal         4.0                   4   
2      710561  Manchester United         8.0                   8   
3      710561              Leeds         3.0                   3   
4      710565            Watford         7.0                   7   

   home_possession  home_passes  home_passes_accuracy  home_fouls  \
0             35.0          309                 201.0          12   
1             65.0          568                 488.0           8   
2             49.0          422                 334.0          11   
3             51.0          438                 343.0           9   
4             38.0          317                 234.0          18   

   home_corners  home_yellow_cards  home_red_cards  
0             2                NaN             NaN  
1             5                NaN             NaN  
2             5                1.0             NaN  
3             4                2.0             NaN  
4             2                3.0             NaN

In [11]:
# アウェイチーム用統計
away_stats = stats_df.copy()
away_stats = away_stats.rename(columns={
    "team_name": "away_team_name",
    "shots": "away_shots",
    "shots_on_goal": "away_shots_on_goal",
    "possession": "away_possession",
    "passes": "away_passes",
    "passes_accuracy": "away_passes_accuracy",
    "fouls": "away_fouls",
    "corners": "away_corners",
    "yellow_cards": "away_yellow_cards",
    "red_cards": "away_red_cards"
})
away_stats = away_stats[["fixture_id", "away_team_name", "away_shots", "away_shots_on_goal",
                         "away_possession", "away_passes", "away_passes_accuracy",
                         "away_fouls", "away_corners", "away_yellow_cards", "away_red_cards"]]

In [12]:
away_stats.head()

fixture_id     away_team_name  away_shots  away_shots_on_goal  \
0      710556          Brentford         3.0                   3   
1      710556            Arsenal         4.0                   4   
2      710561  Manchester United         8.0                   8   
3      710561              Leeds         3.0                   3   
4      710565            Watford         7.0                   7   

   away_possession  away_passes  away_passes_accuracy  away_fouls  \
0             35.0          309                 201.0          12   
1             65.0          568                 488.0           8   
2             49.0          422                 334.0          11   
3             51.0          438                 343.0           9   
4             38.0          317                 234.0          18   

   away_corners  away_yellow_cards  away_red_cards  
0             2                NaN             NaN  
1             5                NaN             NaN  
2             5                1.0             NaN  
3             4                2.0             NaN  
4             2                3.0             NaN

In [13]:
# matches にホーム統計を結合
merged_df = matches_df.merge(home_stats, left_on=["fixture_id", "home_team"], right_on=["fixture_id", "home_team_name"], how="left")

# matches にアウェイ統計を結合
merged_df = merged_df.merge(away_stats, left_on=["fixture_id", "away_team"], right_on=["fixture_id", "away_team_name"], how="left")

# 不要な列を削除
merged_df = merged_df.drop(columns=["home_team_name", "away_team_name"])

# 確認
merged_df.head()

fixture_id                       date  season  home_team       away_team  \
0      710556  2021-08-13T19:00:00+00:00    2021  Brentford         Arsenal   
1      710557  2021-08-14T14:00:00+00:00    2021    Burnley        Brighton   
2      710558  2021-08-14T14:00:00+00:00    2021    Chelsea  Crystal Palace   
3      710559  2021-08-14T14:00:00+00:00    2021    Everton     Southampton   
4      710560  2021-08-14T14:00:00+00:00    2021  Leicester          Wolves   

   home_score  away_score status  home_shots  home_shots_on_goal  \
0         2.0         0.0     FT         3.0                 3.0   
1         1.0         2.0     FT         3.0                 3.0   
2         3.0         0.0     FT         6.0                 6.0   
3         3.0         1.0     FT         6.0                 6.0   
4         1.0         0.0     FT         5.0                 5.0   

   home_possession  home_passes  home_passes_accuracy  home_fouls  \
0             35.0        309.0                 201.0        12.0   
1             36.0        259.0                 181.0        10.0   
2             62.0        678.0                 623.0        15.0   
3             48.0        337.0                 235.0        13.0   
4             56.0        584.0                 505.0         6.0   

   home_corners  home_yellow_cards  home_red_cards  away_shots  \
0           2.0                NaN             NaN         4.0   
1           7.0                2.0             NaN         8.0   
2           5.0                NaN             NaN         1.0   
3           6.0                2.0             NaN         3.0   
4           5.0                1.0             NaN         3.0   

   away_shots_on_goal  away_possession  away_passes  away_passes_accuracy  \
0                 4.0             65.0        568.0                 488.0   
1                 8.0             64.0        518.0                 424.0   
2                 1.0             38.0        423.0                 363.0   
3                 3.0             52.0        370.0                 256.0   
4                 3.0             44.0        443.0                 366.0   

   away_fouls  away_corners  away_yellow_cards  away_red_cards  
0         8.0           5.0                NaN             NaN  
1         7.0           6.0                1.0             NaN  
2        11.0           2.0                NaN             NaN  
3        15.0           8.0                0.0             NaN  
4        10.0           4.0                2.0             NaN

In [14]:
merged_df.isnull().sum()

fixture_id                 0
date                       0
season                     0
home_team                  0
away_team                  0
home_score               250
away_score               250
status                     0
home_shots               760
home_shots_on_goal       250
home_possession          250
home_passes              250
home_passes_accuracy     250
home_fouls               250
home_corners             250
home_yellow_cards        319
home_red_cards          1716
away_shots               760
away_shots_on_goal       250
away_possession          250
away_passes              250
away_passes_accuracy     250
away_fouls               250
away_corners             250
away_yellow_cards        319
away_red_cards          1716
dtype: int64

In [15]:
print(merged_df["status"].unique())
print(merged_df["status"].value_counts())

['FT' 'NS']
status
FT    1650
NS     250
Name: count, dtype: int64


# FTのデータのみ欠損値処理 & 再結合　
statusがFTのデータとNSのデータに分割し、FTのデータのみ欠損値処理することで、  
まだ試合が行われていないNSの欠損値は埋めないようにする

In [16]:
merged_df_FT = merged_df[merged_df["status"] == "FT"]
merged_df_NS = merged_df[merged_df["status"] == "NS"]

print("merged_df_FT")
print("the number of merged_df_FT",len(merged_df_FT))
print(merged_df_FT["status"].unique())
print()
print("merged_df_NS")
print("the number of merged_df_NS",len(merged_df_NS))
print(merged_df_NS["status"].unique())




merged_df_FT
the number of merged_df_FT 1650
['FT']

merged_df_NS
the number of merged_df_NS 250
['NS']


In [17]:
#欠損値のあるカラムの中身確認
null_col = ["home_yellow_cards","home_red_cards","away_yellow_cards","away_red_cards"]

for col in null_col:
    print("column名:",col)
    print(merged_df_FT[col].unique())
    print("uniqueな値の数:",len(merged_df_FT[col].unique()))
    print(merged_df_FT[merged_df_FT[col] == 0]["fixture_id"].count())
    print()

column名: home_yellow_cards
[nan  2.  1.  3.  4.  0.  5.  6.  7.]
uniqueな値の数: 9
211

column名: home_red_cards
[nan  0.  1.  2.]
uniqueな値の数: 4
87

column名: away_yellow_cards
[nan  1.  0.  2.  4.  3.  5.  7.  6.  8.]
uniqueな値の数: 10
141

column名: away_red_cards
[nan  1.  0.  2.]
uniqueな値の数: 4
88



In [18]:
merged_df_FT.isnull().sum()

fixture_id                 0
date                       0
season                     0
home_team                  0
away_team                  0
home_score                 0
away_score                 0
status                     0
home_shots               510
home_shots_on_goal         0
home_possession            0
home_passes                0
home_passes_accuracy       0
home_fouls                 0
home_corners               0
home_yellow_cards         69
home_red_cards          1466
away_shots               510
away_shots_on_goal         0
away_possession            0
away_passes                0
away_passes_accuracy       0
away_fouls                 0
away_corners               0
away_yellow_cards         69
away_red_cards          1466
dtype: int64

In [19]:
# イエローカードとレッドカードは、ホームチームがNanのときは、アウェイチームも必ずNanになっている。カードの枚数はお互いで同じでさえあれば、試合の公平さは保たれるため、すべて0で埋めてしまう。
# home_shotsとaway_shotsのカラムは使わないカラムであり、あとでdropするので、適当に0で埋めてしまっていい。よって、statusがFTのデータのNanはすべて0で埋めてしまう。

merged_df_FT = merged_df_FT.fillna(0)

In [20]:
merged_df_FT.isnull().sum()

fixture_id              0
date                    0
season                  0
home_team               0
away_team               0
home_score              0
away_score              0
status                  0
home_shots              0
home_shots_on_goal      0
home_possession         0
home_passes             0
home_passes_accuracy    0
home_fouls              0
home_corners            0
home_yellow_cards       0
home_red_cards          0
away_shots              0
away_shots_on_goal      0
away_possession         0
away_passes             0
away_passes_accuracy    0
away_fouls              0
away_corners            0
away_yellow_cards       0
away_red_cards          0
dtype: int64

In [21]:
#欠損値のあるカラムの中身確認
#カードの枚数が0になっている数がhomeとawayで同じ数だけ、fillna前と比べて増えているか確認
null_col = ["home_yellow_cards","home_red_cards","away_yellow_cards","away_red_cards"]

for col in null_col:
    print("column名:",col)
    print(merged_df_FT[col].unique())
    print("uniqueな値の数:",len(merged_df_FT[col].unique()))
    print(merged_df_FT[merged_df_FT[col] == 0]["fixture_id"].count())
    print()

column名: home_yellow_cards
[0. 2. 1. 3. 4. 5. 6. 7.]
uniqueな値の数: 8
280

column名: home_red_cards
[0. 1. 2.]
uniqueな値の数: 3
1553

column名: away_yellow_cards
[0. 1. 2. 4. 3. 5. 7. 6. 8.]
uniqueな値の数: 9
210

column名: away_red_cards
[0. 1. 2.]
uniqueな値の数: 3
1554



In [22]:
merged_df = pd.concat([merged_df_FT,merged_df_NS])

merged_df

fixture_id                       date  season          home_team  \
0         710556  2021-08-13T19:00:00+00:00    2021          Brentford   
1         710557  2021-08-14T14:00:00+00:00    2021            Burnley   
2         710558  2021-08-14T14:00:00+00:00    2021            Chelsea   
3         710559  2021-08-14T14:00:00+00:00    2021            Everton   
4         710560  2021-08-14T14:00:00+00:00    2021          Leicester   
5         710561  2021-08-14T11:30:00+00:00    2021  Manchester United   
6         710562  2021-08-15T13:00:00+00:00    2021          Newcastle   
7         710563  2021-08-14T16:30:00+00:00    2021            Norwich   
8         710564  2021-08-15T15:30:00+00:00    2021          Tottenham   
9         710565  2021-08-14T14:00:00+00:00    2021            Watford   
10        710566  2021-08-22T15:30:00+00:00    2021            Arsenal   
11        710567  2021-08-21T14:00:00+00:00    2021        Aston Villa   
12        710568  2021-08-21T16:30:00+00:00    2021           Brighton   
13        710569  2021-08-21T14:00:00+00:00    2021     Crystal Palace   
14        710570  2021-08-21T14:00:00+00:00    2021              Leeds   
15        710571  2021-08-21T11:30:00+00:00    2021          Liverpool   
16        710572  2021-08-21T14:00:00+00:00    2021    Manchester City   
17        710573  2021-08-22T13:00:00+00:00    2021        Southampton   
18        710574  2021-08-23T19:00:00+00:00    2021           West Ham   
19        710575  2021-08-22T13:00:00+00:00    2021             Wolves   
20        710576  2021-08-28T14:00:00+00:00    2021        Aston Villa   
21        710577  2021-08-28T14:00:00+00:00    2021           Brighton   
22        710578  2021-08-29T13:00:00+00:00    2021            Burnley   
23        710579  2021-08-28T16:30:00+00:00    2021          Liverpool   
24        710580  2021-08-28T11:30:00+00:00    2021    Manchester City   
25        710581  2021-08-28T14:00:00+00:00    2021          Newcastle   
26        710582  2021-08-28T14:00:00+00:00    2021            Norwich   
27        710583  2021-08-29T13:00:00+00:00    2021          Tottenham   
28        710584  2021-08-28T14:00:00+00:00    2021           West Ham   
29        710585  2021-08-29T15:30:00+00:00    2021             Wolves   
30        710586  2021-09-11T14:00:00+00:00    2021            Arsenal   
31        710587  2021-09-11T14:00:00+00:00    2021          Brentford   
32        710588  2021-09-11T16:30:00+00:00    2021            Chelsea   
33        710589  2021-09-11T11:30:00+00:00    2021     Crystal Palace   
34        710590  2021-09-13T19:00:00+00:00    2021            Everton   
35        710591  2021-09-12T15:30:00+00:00    2021              Leeds   
36        710592  2021-09-11T14:00:00+00:00    2021          Leicester   
37        710593  2021-09-11T14:00:00+00:00    2021  Manchester United   
38        710594  2021-09-11T14:00:00+00:00    2021        Southampton   
39        710595  2021-09-11T14:00:00+00:00    2021            Watford   
40        710596  2021-09-18T16:30:00+00:00    2021        Aston Villa   
41        710597  2021-09-19T13:00:00+00:00    2021           Brighton   
42        710598  2021-09-18T14:00:00+00:00    2021            Burnley   
43        710599  2021-09-18T14:00:00+00:00    2021          Liverpool   
44        710600  2021-09-18T14:00:00+00:00    2021    Manchester City   
45        710601  2021-09-17T19:00:00+00:00    2021          Newcastle   
46        710602  2021-09-18T14:00:00+00:00    2021            Norwich   
47        710603  2021-09-19T15:30:00+00:00    2021          Tottenham   
48        710604  2021-09-19T13:00:00+00:00    2021           West Ham   
49        710605  2021-09-18T11:30:00+00:00    2021             Wolves   
50        710606  2021-09-26T15:30:00+00:00    2021            Arsenal   
51        710607  2021-09-25T16:30:00+00:00    2021          Brentford   
52        710608  2021-09-25T11:30:00+00:00    2021            Chelsea   
53        

# 再結合後のデータフレームの探索

In [23]:
#カテゴリカルなカラムのuniqueな値を確認
cat_col = ["home_team","away_team","status"]

for col in cat_col:
    print("column名:",col)
    print(merged_df[col].unique())
    print("uniqueな値の数:",len(merged_df[col].unique()))
    print()

column名: home_team
['Brentford' 'Burnley' 'Chelsea' 'Everton' 'Leicester' 'Manchester United'
 'Newcastle' 'Norwich' 'Tottenham' 'Watford' 'Arsenal' 'Aston Villa'
 'Brighton' 'Crystal Palace' 'Leeds' 'Liverpool' 'Manchester City'
 'Southampton' 'West Ham' 'Wolves' 'Fulham' 'Bournemouth'
 'Nottingham Forest' 'Sheffield Utd' 'Luton' 'Ipswich' 'Sunderland']
uniqueな値の数: 27

column名: away_team
['Arsenal' 'Brighton' 'Crystal Palace' 'Southampton' 'Wolves' 'Leeds'
 'West Ham' 'Liverpool' 'Manchester City' 'Aston Villa' 'Chelsea'
 'Newcastle' 'Watford' 'Brentford' 'Everton' 'Burnley' 'Norwich'
 'Manchester United' 'Leicester' 'Tottenham' 'Nottingham Forest'
 'Bournemouth' 'Fulham' 'Luton' 'Sheffield Utd' 'Ipswich' 'Sunderland']
uniqueな値の数: 27

column名: status
['FT' 'NS']
uniqueな値の数: 2



In [24]:
merged_df['date'] = pd.to_datetime(merged_df['date'], errors='coerce')


In [25]:
merged_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1900 entries, 0 to 1899
Data columns (total 26 columns):
 #   Column                Non-Null Count  Dtype              
---  ------                --------------  -----              
 0   fixture_id            1900 non-null   int64              
 1   date                  1900 non-null   datetime64[ns, UTC]
 2   season                1900 non-null   int64              
 3   home_team             1900 non-null   object             
 4   away_team             1900 non-null   object             
 5   home_score            1650 non-null   float64            
 6   away_score            1650 non-null   float64            
 7   status                1900 non-null   object             
 8   home_shots            1650 non-null   float64            
 9   home_shots_on_goal    1650 non-null   float64            
 10  home_possession       1650 non-null   float64            
 11  home_passes           1650 non-null   float64            
 12  home_passes

In [26]:
merged_df.describe()

fixture_id       season   home_score   away_score   home_shots  \
count  1.900000e+03  1900.000000  1650.000000  1650.000000  1650.000000   
mean   1.040314e+06  2023.000000     1.612727     1.342424     3.463030   
std    2.372506e+05     1.414586     1.340586     1.219791     3.216114   
min    7.105560e+05  2021.000000     0.000000     0.000000     0.000000   
25%    8.680408e+05  2022.000000     1.000000     0.000000     0.000000   
50%    1.035364e+06  2023.000000     1.000000     1.000000     3.000000   
75%    1.208307e+06  2024.000000     2.000000     2.000000     6.000000   
max    1.379348e+06  2025.000000     9.000000     8.000000    15.000000   

       home_shots_on_goal  home_possession  home_passes  home_passes_accuracy  \
count         1650.000000      1650.000000  1650.000000           1650.000000   
mean             4.932727        50.917576   460.924242            380.421818   
std              2.610741        12.661301   131.564909            134.283600   
min              0.000000        18.000000   161.000000             80.000000   
25%              3.000000        41.000000   363.250000            279.250000   
50%              5.000000        51.000000   450.000000            369.500000   
75%              6.000000        60.000000   549.000000            466.000000   
max             16.000000        83.000000  1000.000000            944.000000   

        home_fouls  home_corners  home_yellow_cards  home_red_cards  \
count  1650.000000   1650.000000        1650.000000     1650.000000   
mean     10.585455      5.657576           1.828485        0.061818   
std       3.467990      3.101627           1.361442        0.253172   
min       1.000000      0.000000           0.000000        0.000000   
25%       8.000000      3.000000           1.000000        0.000000   
50%      10.000000      5.000000           2.000000        0.000000   
75%      13.000000      8.000000           3.000000        0.000000   
max      23.000000     17.000000           7.000000        2.000000   

        away_shots  away_shots_on_goal  away_possession  away_passes  \
count  1650.000000         1650.000000      1650.000000  1650.000000   
mean      2.875152            4.143030        49.082424   446.498182   
std       2.810390            2.404797        12.661301   127.548453   
min       0.000000            0.000000        17.000000   148.000000   
25%       0.000000            2.000000        40.000000   350.250000   
50%       3.000000            4.000000        49.000000   435.500000   
75%       5.000000            5.000000        59.000000   528.000000   
max      15.000000           15.000000        82.000000   895.000000   

       away_passes_accuracy   away_fouls  away_corners  away_yellow_cards  \
count           1650.000000  1650.000000   1650.000000        1650.000000   
mean             365.217576    10.975758      4.681818           2.096364   
std              128.954129     3.614121      2.861674           1.417143   
min               78.000000     0.000000      0.000000           0.000000   
25%              266.000000     8.000000      3.000000           1.000000   
50%              353.500000    11.000000      4.000000           2.000000   
75%              448.750000    13.000000      6.000000           3.000000   
max              827.000000    25.000000     19.000000           8.000000   

       away_red_cards  
count     1650.000000  
mean         0.058788  
std          0.237862  
min          0.000000  
25%          0.000000  
50%          0.000000  
75%          0.000000  
max          2.000000

In [27]:
#shotsカラムとshots on goalカラムの値が全く同じになっているため、shotsカラムををdropする
merged_df = merged_df.drop(columns = ["home_shots","away_shots"],axis = 1)

merged_df.columns

Index(['fixture_id', 'date', 'season', 'home_team', 'away_team', 'home_score',
       'away_score', 'status', 'home_shots_on_goal', 'home_possession',
       'home_passes', 'home_passes_accuracy', 'home_fouls', 'home_corners',
       'home_yellow_cards', 'home_red_cards', 'away_shots_on_goal',
       'away_possession', 'away_passes', 'away_passes_accuracy', 'away_fouls',
       'away_corners', 'away_yellow_cards', 'away_red_cards'],
      dtype='object')

# 過去シーズンのデータを結合

In [28]:
# ----------------------------------------------------
# 4. 過去シーズンのデータを結合（昇格チームの欠損値処理も含む）
# ----------------------------------------------------

# try:
#     # 過去シーズンのデータを読み込み
#     season_df = pd.read_csv("premier_league.csv")
#     season_df = season_df.drop(columns = ["played","notes"],axis = 1)
# except FileNotFoundError:
#     print("エラー: 'premier_league.csv' が見つかりません。過去シーズン成績の結合をスキップします。")
#     return df # ファイルがない場合は結合せずにそのまま返す

# # 2つのデータフレームのチーム名の表記の仕方をそろえる
# mapping = {'Manchester City':'Manchester City','Manchester Utd':'Manchester United','Liverpool':'Liverpool','Chelsea':'Chelsea',
#           'Leicester City':'Leicester','West Ham':'West Ham','Tottenham':'Tottenham','Arsenal':'Arsenal','Leeds United':'Leeds',
#           'Everton':'Everton','Aston Villa':'Aston Villa','Newcastle Utd':'Newcastle','Wolves':'Wolves','Crystal Palace':'Crystal Palace',
#           'Southampton':'Southampton','Brighton':'Brighton','Burnley':'Burnley','Fulham':'Fulham','Sheffield Utd':'Sheffield Utd',
#           'Brentford':'Brentford','Watford':'Watford','Norwich City':'Norwich','Bournemouth':'Bournemouth','Nottingham Forest':'Nottingham Forest','Luton Town':'Luton','Ipswich':'Ipswich'}    

#  # チーム名の表記を統一
# season_df["team"] = season_df["team"].replace(mapping) 


# # --- 結合後の新しいカラム名の定義 ---
# # premier_league.csv の 'points' のリネーム
# season_col_map = {
#     "points":"last_points", 
#     "position":"last_position", "won":"last_won", "drawn":"last_drawn", 
#     "lost":"last_lost", "gf":"last_gf", "ga":"last_ga", "gd":"last_gd"
# }

# # 1. ホームチームとして結合するためのデータ準備
# season_home_df = season_df.rename(columns = season_col_map)
# season_home_df = season_home_df.rename(columns = {
#     "season_end_year":"season", "team":"home_team",
# })

# # 結合後の列名に 'home_' 接頭辞を付加
# new_home_cols = {v: f"home_{v}" for v in season_col_map.values()}
# season_home_df = season_home_df.rename(columns = new_home_cols)

# # 2. アウェイチームとして結合するためのデータ準備
# season_away_df = season_df.rename(columns = season_col_map)
# season_away_df = season_away_df.rename(columns = {
#     "season_end_year":"season", "team":"away_team",
# })

# # 結合後の列名に 'away_' 接頭辞を付加
# new_away_cols = {v: f"away_{v}" for v in season_col_map.values()}
# season_away_df = season_away_df.rename(columns = new_away_cols)

# # --- 結合ロジック ---
# df = pd.merge(df, season_home_df, on = ["season","home_team"], how = "left")
# df = pd.merge(df, season_away_df, on = ["season","away_team"], how = "left")
# # この時点で、dfには 'home_last_points' などが追加され、昇格組は NaN

# ----------------------------------------------------
# 5. 昇格組の欠損値処理（各試合の【結合済みの前シーズン】の17位の値で埋める）
# ----------------------------------------------------

# # 欠損値を埋める対象となる、season_df内の【元の列名】
# original_cols = list(season_col_map.keys()) # ['points', 'position', 'won', 'drawn', ...]

# # 試合のシーズンごとに欠損値の埋め立てを実行
# for target_season in df['season'].unique():
#     # target_season は試合が行われるシーズンの終了年 (例: 2025年)
#     # season_dfの target_season の行は、その試合の前シーズンの成績 (2025年終了のシーズン)
    
#     # 17位チームの成績を取得
#     relegation_avoidance_team = season_df[
#         (season_df["season_end_year"] == target_season) & 
#         (season_df["position"] == 17)
#     ]
    
#     # 代理値ルックアップテーブルを作成
#     fill_values = {}
#     if not relegation_avoidance_team.empty:
#         for original_col in original_cols:
#             # 17位の成績をそのまま取得
#             val = relegation_avoidance_team[original_col].iloc[0] 
            
#             # 結合後のカラム名（ home_last_points など）を生成
#             new_suffix = season_col_map[original_col] 
            
#             fill_values[f'home_{new_suffix}'] = val
#             fill_values[f'away_{new_suffix}'] = val
#     else:
#          print(f"警告: シーズン {target_season} の17位のデータが見つかりませんでした。このシーズンの昇格組の処理をスキップします。")
#          continue
    
#     # このシーズン（target_season）の試合に限定して欠損値を埋める
#     target_fill_cols = list(fill_values.keys())

#     # 欠損値（昇格組）に対してのみ、17位の値で埋める
#     for full_col_name in target_fill_cols:
#         is_target_season = df['season'] == target_season
#         is_nan = df[full_col_name].isna()
        
#         # 論理インデックスを使用して、対象のセルのみに値を代入
#         df.loc[is_target_season & is_nan, full_col_name] = fill_values[full_col_name]


# ----------------------------------------------------
# 6. データタイプの変換と列の削除
# ----------------------------------------------------

# # dateカラムのデータタイプをdatetimeに変換
# df['date'] = pd.to_datetime(df['date'], errors='coerce')

# # shotsカラムとshots on goalカラムの値が全く同じになっているため、shotsカラムををdropする
# df = df.drop(columns = ["home_shots","away_shots"], axis = 1, errors='ignore')

In [29]:
# season_df = pd.read_csv("premier_league.csv")
# season_df = season_df.drop(columns = ["played","notes"],axis = 1)

# ----------------------------------------------------
# 4. 過去シーズンのデータを結合（昇格チームの欠損値処理も含む）
# ----------------------------------------------------

try:
    # 過去シーズンのデータを読み込み
    season_df = pd.read_csv(SEASON_DATA_PATH)
    season_df = season_df.drop(columns = ["played","notes"],axis = 1)
except FileNotFoundError:
    print("エラー: 'premier_league.csv' が見つかりません。過去シーズン成績の結合をスキップします。")
    # return df # ファイルがない場合は結合せずにそのまま返す


print(season_df[(season_df["season_end_year"] == 2021) | (season_df["season_end_year"] == 2022) | (season_df["season_end_year"] == 2023)| 
      (season_df["season_end_year"] == 2024)| (season_df["season_end_year"] == 2025)]["team"].unique())
print(merged_df["home_team"].unique())

['Manchester City' 'Manchester Utd' 'Liverpool' 'Chelsea' 'Leicester City'
 'West Ham' 'Tottenham' 'Arsenal' 'Leeds United' 'Everton' 'Aston Villa'
 'Newcastle Utd' 'Wolves' 'Crystal Palace' 'Southampton' 'Brighton'
 'Burnley' 'Fulham' 'West Brom' 'Sheffield Utd' 'Brentford' 'Watford'
 'Norwich City' 'Bournemouth' 'Nottingham Forest' 'Luton Town' 'Ipswich']
['Brentford' 'Burnley' 'Chelsea' 'Everton' 'Leicester' 'Manchester United'
 'Newcastle' 'Norwich' 'Tottenham' 'Watford' 'Arsenal' 'Aston Villa'
 'Brighton' 'Crystal Palace' 'Leeds' 'Liverpool' 'Manchester City'
 'Southampton' 'West Ham' 'Wolves' 'Fulham' 'Bournemouth'
 'Nottingham Forest' 'Sheffield Utd' 'Luton' 'Ipswich' 'Sunderland']


In [30]:
# 2つのデータフレームのチーム名の表記の仕方をそろえる
mapping = {'Manchester City':'Manchester City','Manchester Utd':'Manchester United','Liverpool':'Liverpool','Chelsea':'Chelsea',
          'Leicester City':'Leicester','West Ham':'West Ham','Tottenham':'Tottenham','Arsenal':'Arsenal','Leeds United':'Leeds',
          'Everton':'Everton','Aston Villa':'Aston Villa','Newcastle Utd':'Newcastle','Wolves':'Wolves','Crystal Palace':'Crystal Palace',
          'Southampton':'Southampton','Brighton':'Brighton','Burnley':'Burnley','Fulham':'Fulham','Sheffield Utd':'Sheffield Utd',
          'Brentford':'Brentford','Watford':'Watford','Norwich City':'Norwich','Bournemouth':'Bournemouth','Nottingham Forest':'Nottingham Forest','Luton Town':'Luton','Ipswich':'Ipswich'}

season_df["team"] = season_df["team"].replace(mapping) 

In [31]:
# season_home_df = season_df.rename(columns = {"season_end_year":"season","team":"home_team","points":"home_last_points",
#                                             "position":"home_last_position","won":"home_last_won","drawn":"home_last_drawn","lost":"home_last_lost",
#                                              "gf":"home_last_gf","ga":"home_last_ga","gd":"home_last_gd"})

# season_away_df = season_df.rename(columns = {"season_end_year":"season","team":"away_team","points":"away_last_points",
#                                             "position":"away_last_position","won":"away_last_won","drawn":"away_last_drawn","lost":"away_last_lost",
#                                              "gf":"away_last_gf","ga":"away_last_ga","gd":"away_last_gd"})

# season_home_df.columns

# season_home_df[['home_last_position', 'home_last_won','home_last_drawn', 'home_last_lost',
#              'home_last_gf', 'home_last_ga','home_last_gd', 'home_last_points']] = season_home_df[['home_last_position', 'home_last_won',
#                                                                                     'home_last_drawn', 'home_last_lost', 'home_last_gf', 'home_last_ga',
#                                                                                     'home_last_gd', 'home_last_points']].astype(int)

# season_away_df[['away_last_position', 'away_last_won','away_last_drawn', 'away_last_lost',
#              'away_last_gf', 'away_last_ga','away_last_gd', 'away_last_points']] = season_away_df[['away_last_position', 'away_last_won',
#                                                                                     'away_last_drawn', 'away_last_lost', 'away_last_gf', 'away_last_ga',
#                                                                                     'away_last_gd', 'away_last_points']].astype(int)


# --- 結合後の新しいカラム名の定義 ---
# premier_league.csv の 'points' のリネーム
season_col_map = {
    "points":"last_points", 
    "position":"last_position", "won":"last_won", "drawn":"last_drawn", 
    "lost":"last_lost", "gf":"last_gf", "ga":"last_ga", "gd":"last_gd"
}

# 1. ホームチームとして結合するためのデータ準備
season_home_df = season_df.rename(columns = season_col_map)
season_home_df = season_home_df.rename(columns = {
    "season_end_year":"season", "team":"home_team",
})

# 結合後の列名に 'home_' 接頭辞を付加
new_home_cols = {v: f"home_{v}" for v in season_col_map.values()}
season_home_df = season_home_df.rename(columns = new_home_cols)

# 2. アウェイチームとして結合するためのデータ準備
season_away_df = season_df.rename(columns = season_col_map)
season_away_df = season_away_df.rename(columns = {
    "season_end_year":"season", "team":"away_team",
})

# 結合後の列名に 'away_' 接頭辞を付加
new_away_cols = {v: f"away_{v}" for v in season_col_map.values()}
season_away_df = season_away_df.rename(columns = new_away_cols)

In [32]:
merged_df = pd.merge(
    merged_df,
    season_home_df,
    on = ["season","home_team"],
    how = "left"
)

merged_df = pd.merge(
    merged_df,
    season_away_df,
    on = ["season","away_team"],
    how = "left"
)

# merged_df[['season', 'home_team', 'position', 'won', 'drawn', 'lost', 'gf', 'ga',
#        'gd', 'previous_points']][merged_df["home_team"] == "Brentford"]

merged_df.head()

fixture_id                      date  season  home_team       away_team  \
0      710556 2021-08-13 19:00:00+00:00    2021  Brentford         Arsenal   
1      710557 2021-08-14 14:00:00+00:00    2021    Burnley        Brighton   
2      710558 2021-08-14 14:00:00+00:00    2021    Chelsea  Crystal Palace   
3      710559 2021-08-14 14:00:00+00:00    2021    Everton     Southampton   
4      710560 2021-08-14 14:00:00+00:00    2021  Leicester          Wolves   

   home_score  away_score status  home_shots_on_goal  home_possession  \
0         2.0         0.0     FT                 3.0             35.0   
1         1.0         2.0     FT                 3.0             36.0   
2         3.0         0.0     FT                 6.0             62.0   
3         3.0         1.0     FT                 6.0             48.0   
4         1.0         0.0     FT                 5.0             56.0   

   home_passes  home_passes_accuracy  home_fouls  home_corners  \
0        309.0                 201.0        12.0           2.0   
1        259.0                 181.0        10.0           7.0   
2        678.0                 623.0        15.0           5.0   
3        337.0                 235.0        13.0           6.0   
4        584.0                 505.0         6.0           5.0   

   home_yellow_cards  home_red_cards  away_shots_on_goal  away_possession  \
0                0.0             0.0                 4.0             65.0   
1                2.0             0.0                 8.0             64.0   
2                0.0             0.0                 1.0             38.0   
3                2.0             0.0                 3.0             52.0   
4                1.0             0.0                 3.0             44.0   

   away_passes  away_passes_accuracy  away_fouls  away_corners  \
0        568.0                 488.0         8.0           5.0   
1        518.0                 424.0         7.0           6.0   
2        423.0                 363.0        11.0           2.0   
3        370.0                 256.0        15.0           8.0   
4        443.0                 366.0        10.0           4.0   

   away_yellow_cards  away_red_cards  home_last_position  home_last_won  \
0                0.0             0.0                 NaN            NaN   
1                1.0             0.0                17.0           10.0   
2                0.0             0.0                 4.0           19.0   
3                0.0             0.0                10.0           17.0   
4                2.0             0.0                 5.0           20.0   

   home_last_drawn  home_last_lost  home_last_gf  home_last_ga  home_last_gd  \
0              NaN             NaN           NaN           NaN           NaN   
1              9.0            19.0          33.0          55.0         -22.0   
2             10.0             9.0          58.0          36.0          22.0   
3              8.0            13.0          47.0          48.0          -1.0   
4              6.0            12.0          68.0          50.0          18.0   

   home_last_points  away_last_position  away_last_won  away_last_drawn  \
0               NaN                 8.0           18.0              7.0   
1              39.0                16.0            9.0             14.0   
2              67.0                14.0           12.0              8.0   
3              59.0                15.0           12.0              7.0   
4              66.0                13.0           12.0              9.0   

   away_last_lost  away_last_gf  away_last_ga  away_last_gd  away_last_points  
0            13.0          55.0          39.0          16.0              61.0  
1            15.0          40.0          46.0          -6.0              41.0  
2            18.0          41.0          66.0         -25.0              44.0  
3            19.0          47.0          68.0         -21.0              43.0  
4            17.0          36.0          52.0         -

In [33]:
# columns = ['home_last_position', 'home_last_won','home_last_drawn', 'home_last_lost','home_last_gf', 'home_last_ga','home_last_gd', 'home_last_points']
# seasons = [2021,2022,2023,2024,2025]
# season_min = []


# for season in seasons:
#     for col in columns:
#         season_min.append({
#             "season":season,
#             "column":col,
#             "min":season_home_df[season_home_df["season"] == season][col].min()
#         })

# season_min_df = pd.DataFrame(season_min)

# season_min_df

In [34]:
relegation_avoidance_team = season_df[
        (season_df["season_end_year"] == 2024) & 
        (season_df["position"] == 17)
    ]

relegation_avoidance_team

season_end_year               team  position  won  drawn  lost  gf  ga  \
642             2024  Nottingham Forest        17    9      9    20  49  67   

     gd  points  
642 -18      32

In [35]:
# 欠損値を埋める対象となる、season_df内の【元の列名】
original_cols = list(season_col_map.keys()) # ['points', 'position', 'won', 'drawn', ...]

# 試合のシーズンごとに欠損値の埋め立てを実行
for target_season in merged_df['season'].unique():
    # target_season は試合が行われるシーズンの終了年 (例: 2025年)
    # season_dfの target_season の行は、その試合の前シーズンの成績 (2025年終了のシーズン)
    
    # 17位チームの成績を取得
    relegation_avoidance_team = season_df[
        (season_df["season_end_year"] == target_season) & 
        (season_df["position"] == 17)
    ]
    
    # 代理値ルックアップテーブルを作成
    fill_values = {}
    if not relegation_avoidance_team.empty:
        for original_col in original_cols:
            # 17位の成績をそのまま取得
            val = relegation_avoidance_team[original_col].iloc[0] #valは指定のシーズンの前のシーズンにおける17位のチームpositionやwonの値
            
            # 結合後のカラム名（ home_last_points など）を生成
            new_suffix = season_col_map[original_col] 
            
            fill_values[f'home_{new_suffix}'] = val
            fill_values[f'away_{new_suffix}'] = val
    else:
         print(f"警告: シーズン {target_season} の17位のデータが見つかりませんでした。このシーズンの昇格組の処理をスキップします。")
         continue
    
    # このシーズン（target_season）の試合に限定して欠損値を埋める
    target_fill_cols = list(fill_values.keys())

    # 欠損値（昇格組）に対してのみ、17位の値で埋める
    for full_col_name in target_fill_cols:
        is_target_season = merged_df['season'] == target_season
        is_nan = merged_df[full_col_name].isna()
        
        # 論理インデックスを使用して、対象のセルのみに値を代入
        merged_df.loc[is_target_season & is_nan, full_col_name] = fill_values[full_col_name]

In [36]:
print(season_col_map["position"])
print(fill_values)
print(target_fill_cols)
print(is_target_season)
print(is_nan)
print(fill_values["home_last_points"])
print(merged_df.loc[is_target_season & is_nan, "home_last_points"])

last_position
{'home_last_points': np.int64(38), 'away_last_points': np.int64(38), 'home_last_position': np.int64(17), 'away_last_position': np.int64(17), 'home_last_won': np.int64(11), 'away_last_won': np.int64(11), 'home_last_drawn': np.int64(5), 'away_last_drawn': np.int64(5), 'home_last_lost': np.int64(22), 'away_last_lost': np.int64(22), 'home_last_gf': np.int64(64), 'away_last_gf': np.int64(64), 'home_last_ga': np.int64(65), 'away_last_ga': np.int64(65), 'home_last_gd': np.int64(-1), 'away_last_gd': np.int64(-1)}
['home_last_points', 'away_last_points', 'home_last_position', 'away_last_position', 'home_last_won', 'away_last_won', 'home_last_drawn', 'away_last_drawn', 'home_last_lost', 'away_last_lost', 'home_last_gf', 'away_last_gf', 'home_last_ga', 'away_last_ga', 'home_last_gd', 'away_last_gd']
0       False
1       False
2       False
3       False
4       False
5       False
6       False
7       False
8       False
9       False
10      False
11      False
12      False
13  

In [37]:
season_home_df.columns

Index(['season', 'home_team', 'home_last_position', 'home_last_won',
       'home_last_drawn', 'home_last_lost', 'home_last_gf', 'home_last_ga',
       'home_last_gd', 'home_last_points'],
      dtype='object')

In [38]:
merged_df[["season","home_team","away_team",'home_last_position', 'home_last_won',
       'home_last_drawn', 'home_last_lost', 'home_last_gf', 'home_last_ga',
       'home_last_gd', 'home_last_points']]

season          home_team          away_team  home_last_position  \
0       2021          Brentford            Arsenal                17.0   
1       2021            Burnley           Brighton                17.0   
2       2021            Chelsea     Crystal Palace                 4.0   
3       2021            Everton        Southampton                10.0   
4       2021          Leicester             Wolves                 5.0   
5       2021  Manchester United              Leeds                 2.0   
6       2021          Newcastle           West Ham                12.0   
7       2021            Norwich          Liverpool                17.0   
8       2021          Tottenham    Manchester City                 7.0   
9       2021            Watford        Aston Villa                17.0   
10      2021            Arsenal            Chelsea                 8.0   
11      2021        Aston Villa          Newcastle                11.0   
12      2021           Brighton            Watford                16.0   
13      2021     Crystal Palace          Brentford                14.0   
14      2021              Leeds            Everton                 9.0   
15      2021          Liverpool            Burnley                 3.0   
16      2021    Manchester City            Norwich                 1.0   
17      2021        Southampton  Manchester United                15.0   
18      2021           West Ham          Leicester                 6.0   
19      2021             Wolves          Tottenham                13.0   
20      2021        Aston Villa          Brentford                11.0   
21      2021           Brighton            Everton                16.0   
22      2021            Burnley              Leeds                17.0   
23      2021          Liverpool            Chelsea                 3.0   
24      2021    Manchester City            Arsenal                 1.0   
25      2021          Newcastle        Southampton                12.0   
26      2021            Norwich          Leicester                17.0   
27      2021          Tottenham            Watford                 7.0   
28      2021           West Ham     Crystal Palace                 6.0   
29      2021             Wolves  Manchester United                13.0   
30      2021            Arsenal            Norwich                 8.0   
31      2021          Brentford           Brighton                17.0   
32      2021            Chelsea        Aston Villa                 4.0   
33      2021     Crystal Palace          Tottenham                14.0   
34      2021            Everton            Burnley                10.0   
35      2021              Leeds          Liverpool                 9.0   
36      2021          Leicester    Manchester City                 5.0   
37      2021  Manchester United          Newcastle                 2.0   
38      2021        Southampton           West Ham                15.0   
39      2021            Watford             Wolves                17.0   
40      2021        Aston Villa            Everton                11.0   
41      2021           Brighton          Leicester                16.0   
42      2021            Burnley            Arsenal                17.0   
43      2021          Liverpool     Crystal Palace                 3.0   
44      2021    Manchester City        Southampton                 1.0   
45      2021          Newcastle              Leeds                12.0   
46      2021            Norwich            Watford                17.0   
47      2021          Tottenham            Chelsea                 7.0   
48      2021           West Ham  Manchester United                 6.0   
49      2021             Wolves          Brentford                13.0   
50      2021            Arsenal          Tottenham                 8.0   
51      2021          Brentford          Liverpool                17.0   
52      2021            Chelsea    Manchester City                 4.0   
53      20

In [39]:
merged_df.isnull().sum()

fixture_id                0
date                      0
season                    0
home_team                 0
away_team                 0
home_score              250
away_score              250
status                    0
home_shots_on_goal      250
home_possession         250
home_passes             250
home_passes_accuracy    250
home_fouls              250
home_corners            250
home_yellow_cards       250
home_red_cards          250
away_shots_on_goal      250
away_possession         250
away_passes             250
away_passes_accuracy    250
away_fouls              250
away_corners            250
away_yellow_cards       250
away_red_cards          250
home_last_position        0
home_last_won             0
home_last_drawn           0
home_last_lost            0
home_last_gf              0
home_last_ga              0
home_last_gd              0
home_last_points          0
away_last_position        0
away_last_won             0
away_last_drawn           0
away_last_lost      

In [40]:
# season_min_df[(season_min_df["season"] == 2021) & (season_min_df["column"] == "home_last_won")].iloc[0,2]

In [41]:
# merged_df["home_last_position"] = merged_df["home_last_position"].fillna(5)

In [42]:
merged_df[merged_df["home_last_position"] == 17]["home_last_won"].iloc[0]

np.float64(10.0)

In [43]:
# def home_fill_nan(group):
#     columns = ['home_last_won','home_last_drawn', 'home_last_lost','home_last_gf', 'home_last_ga','home_last_gd', 'home_last_points','home_last_position']
#     for col in columns:
#         minimum = group[group["home_last_position"] == 17][col].iloc[0]
#         group[col] = group[col].fillna(minimum)
    
#     return group

# def away_fill_nan(group):
#     columns = ['away_last_won','away_last_drawn', 'away_last_lost','away_last_gf', 'away_last_ga','away_last_gd', 'away_last_points','away_last_position', ]
#     for col in columns:
#         minimum = group[group["away_last_position"] == 17][col].iloc[0]
#         group[col] = group[col].fillna(minimum)
    
#     return group



# merged_df = merged_df.groupby("season").apply(home_fill_nan).reset_index(drop=True)
# merged_df = merged_df.groupby("season").apply(away_fill_nan).reset_index(drop=True)


# merged_df[["season","home_team","away_team",'home_last_position', 'home_last_won','home_last_drawn', 'home_last_lost','home_last_gf', 'home_last_ga','home_last_gd', 'home_last_points',
#               'away_last_position', 'away_last_won','away_last_drawn', 'away_last_lost','away_last_gf', 'away_last_ga','away_last_gd', 'away_last_points']]

In [44]:
merged_df.isnull().sum()

fixture_id                0
date                      0
season                    0
home_team                 0
away_team                 0
home_score              250
away_score              250
status                    0
home_shots_on_goal      250
home_possession         250
home_passes             250
home_passes_accuracy    250
home_fouls              250
home_corners            250
home_yellow_cards       250
home_red_cards          250
away_shots_on_goal      250
away_possession         250
away_passes             250
away_passes_accuracy    250
away_fouls              250
away_corners            250
away_yellow_cards       250
away_red_cards          250
home_last_position        0
home_last_won             0
home_last_drawn           0
home_last_lost            0
home_last_gf              0
home_last_ga              0
home_last_gd              0
home_last_points          0
away_last_position        0
away_last_won             0
away_last_drawn           0
away_last_lost      

In [45]:
merged_df.columns

Index(['fixture_id', 'date', 'season', 'home_team', 'away_team', 'home_score',
       'away_score', 'status', 'home_shots_on_goal', 'home_possession',
       'home_passes', 'home_passes_accuracy', 'home_fouls', 'home_corners',
       'home_yellow_cards', 'home_red_cards', 'away_shots_on_goal',
       'away_possession', 'away_passes', 'away_passes_accuracy', 'away_fouls',
       'away_corners', 'away_yellow_cards', 'away_red_cards',
       'home_last_position', 'home_last_won', 'home_last_drawn',
       'home_last_lost', 'home_last_gf', 'home_last_ga', 'home_last_gd',
       'home_last_points', 'away_last_position', 'away_last_won',
       'away_last_drawn', 'away_last_lost', 'away_last_gf', 'away_last_ga',
       'away_last_gd', 'away_last_points'],
      dtype='object')

In [46]:
merged_df[['home_passes_accuracy','home_yellow_cards', 'home_red_cards','away_passes_accuracy',
            'away_yellow_cards', 'away_red_cards','home_last_position', 'home_last_won', 'home_last_drawn',
            'home_last_lost', 'home_last_gf', 'home_last_ga', 'home_last_gd','home_last_points',
            'away_last_position', 'away_last_won','away_last_drawn', 'away_last_lost', 
            'away_last_gf', 'away_last_ga','away_last_gd', 'away_last_points']] = merged_df[['home_passes_accuracy',
                                                        'home_yellow_cards', 'home_red_cards','away_passes_accuracy',
                                                        'away_yellow_cards', 'away_red_cards','home_last_position', 
                                                        'home_last_won', 'home_last_drawn','home_last_lost', 
                                                        'home_last_gf', 'home_last_ga', 'home_last_gd','home_last_points',
                                                        'away_last_position', 'away_last_won','away_last_drawn', 
                                                        'away_last_lost', 'away_last_gf', 'away_last_ga',
                                                        'away_last_gd', 'away_last_points']].astype("Int64")

In [47]:
merged_df

fixture_id                      date  season          home_team  \
0         710556 2021-08-13 19:00:00+00:00    2021          Brentford   
1         710557 2021-08-14 14:00:00+00:00    2021            Burnley   
2         710558 2021-08-14 14:00:00+00:00    2021            Chelsea   
3         710559 2021-08-14 14:00:00+00:00    2021            Everton   
4         710560 2021-08-14 14:00:00+00:00    2021          Leicester   
5         710561 2021-08-14 11:30:00+00:00    2021  Manchester United   
6         710562 2021-08-15 13:00:00+00:00    2021          Newcastle   
7         710563 2021-08-14 16:30:00+00:00    2021            Norwich   
8         710564 2021-08-15 15:30:00+00:00    2021          Tottenham   
9         710565 2021-08-14 14:00:00+00:00    2021            Watford   
10        710566 2021-08-22 15:30:00+00:00    2021            Arsenal   
11        710567 2021-08-21 14:00:00+00:00    2021        Aston Villa   
12        710568 2021-08-21 16:30:00+00:00    2021           Brighton   
13        710569 2021-08-21 14:00:00+00:00    2021     Crystal Palace   
14        710570 2021-08-21 14:00:00+00:00    2021              Leeds   
15        710571 2021-08-21 11:30:00+00:00    2021          Liverpool   
16        710572 2021-08-21 14:00:00+00:00    2021    Manchester City   
17        710573 2021-08-22 13:00:00+00:00    2021        Southampton   
18        710574 2021-08-23 19:00:00+00:00    2021           West Ham   
19        710575 2021-08-22 13:00:00+00:00    2021             Wolves   
20        710576 2021-08-28 14:00:00+00:00    2021        Aston Villa   
21        710577 2021-08-28 14:00:00+00:00    2021           Brighton   
22        710578 2021-08-29 13:00:00+00:00    2021            Burnley   
23        710579 2021-08-28 16:30:00+00:00    2021          Liverpool   
24        710580 2021-08-28 11:30:00+00:00    2021    Manchester City   
25        710581 2021-08-28 14:00:00+00:00    2021          Newcastle   
26        710582 2021-08-28 14:00:00+00:00    2021            Norwich   
27        710583 2021-08-29 13:00:00+00:00    2021          Tottenham   
28        710584 2021-08-28 14:00:00+00:00    2021           West Ham   
29        710585 2021-08-29 15:30:00+00:00    2021             Wolves   
30        710586 2021-09-11 14:00:00+00:00    2021            Arsenal   
31        710587 2021-09-11 14:00:00+00:00    2021          Brentford   
32        710588 2021-09-11 16:30:00+00:00    2021            Chelsea   
33        710589 2021-09-11 11:30:00+00:00    2021     Crystal Palace   
34        710590 2021-09-13 19:00:00+00:00    2021            Everton   
35        710591 2021-09-12 15:30:00+00:00    2021              Leeds   
36        710592 2021-09-11 14:00:00+00:00    2021          Leicester   
37        710593 2021-09-11 14:00:00+00:00    2021  Manchester United   
38        710594 2021-09-11 14:00:00+00:00    2021        Southampton   
39        710595 2021-09-11 14:00:00+00:00    2021            Watford   
40        710596 2021-09-18 16:30:00+00:00    2021        Aston Villa   
41        710597 2021-09-19 13:00:00+00:00    2021           Brighton   
42        710598 2021-09-18 14:00:00+00:00    2021            Burnley   
43        710599 2021-09-18 14:00:00+00:00    2021          Liverpool   
44        710600 2021-09-18 14:00:00+00:00    2021    Manchester City   
45        710601 2021-09-17 19:00:00+00:00    2021          Newcastle   
46        710602 2021-09-18 14:00:00+00:00    2021            Norwich   
47        710603 2021-09-19 15:30:00+00:00    2021          Tottenham   
48        710604 2021-09-19 13:00:00+00:00    2021           West Ham   
49        710605 2021-09-18 11:30:00+00:00    2021             Wolves   
50        710606 2021-09-26 15:30:00+00:00    2021            Arsenal   
51        710607 2021-09-25 16:30:00+00:00    2021          Brentford   
52        710608 2021-09-25 11:30:00+00:00    2021            Chelsea   
53        710609 2021-09-27 19:00:00+00:00    2021     Crystal P

In [48]:
merged_df.to_csv(CSV_PATH,index = False)